In [ ]:
pip install diffusers torchsde

In [2]:
import os
import pandas as pd
import torch
import gc
import soundfile as sf
from diffusers import StableAudioPipeline

os.environ["HF_TOKEN"] = 'your_hf_token'

In [ ]:
device = "cuda"

pipe = StableAudioPipeline.from_pretrained("stabilityai/stable-audio-open-1.0", torch_dtype=torch.float16)
pipe = pipe.to(device)

negative_prompt = "Low quality."

generator = torch.Generator("cuda").manual_seed(0)

In [7]:
template = "a {} talking"

In [8]:
df = pd.read_csv("/kaggle/input/audio-bias-data/Bias_Types_Term_Category.csv")

In [13]:
def generate_and_save(term, start_idx=0, number=100, batch_size=10):
    descriptions = [template.format(term) for _ in range(number)]

    for batch_start in range(0, len(descriptions), batch_size):
        batch_descriptions = descriptions[batch_start:batch_start + batch_size]

        try:
            audio = pipe(
                batch_descriptions,
                num_inference_steps=4,
                audio_end_in_s=5.0,
                num_waveforms_per_prompt=1,
                generator=generator,
            ).audios

            for idx, one_wav in enumerate(audio):
                wav_data = one_wav.T.float().cpu().numpy()
                sf.write(f'./stable_audio/{term}_{batch_start + idx + start_idx}.wav', wav_data, pipe.vae.sampling_rate)

        except Exception as e:
            print(f"Error processing batch starting at {batch_start}: {e}")

        finally:
            if 'audio' in locals():
                del audio
            gc.collect()


In [ ]:
for idx, rows in df.iterrows():
    if rows['Category'] != 'Religion' and rows['Category'] != 'Portrayal in Media':
      print(rows['Term'], idx+1)
      generate_and_save(rows['Term'], 0, 100, 4)